# Building and analyzing EMMAA Models of Neurofibromatosis

As explained in the README, there are several steps that are used in the assembly of EMMAA models that currently require direct SQL access to the [INDRA Database](https://db.indra.bio). In particular, initializing and updating EMMAA models requires access to user-submitted curations and raw, unpreprocessed statements from the machine reading systems, neither of which are currently accessible via the public REST API of the INDRA Database (accessible at https://db.indra.bio). During the NF Hackathon we didn't have sufficient time to update EMMAA to run off strictly public APIs but we plan to do so in the near future.

With that in mind, in this notebook we show how we initialize the models for deploying to EMMAA, and we illustrate what EMMAA does on the platform to assemble them and generate causal explanations. These are generally the same steps and functions that are run in the AWS Batch jobs generated by the EMMAA system, but instead of reading/writing results to AWS S3 for visualization in the EMMAA web application we create and explore the results in this notebook.

This notebook illustrates the three key parts of our project:
1. Assembling an NF Knowledge Network from text mining results stored in the INDRA Database
2. Assembling a model of Ras-NF mechanisms from natural language descriptions of mechanisms
3. Explaining the causal relations in the text-mined model using the curated model
4. Using both models to explain NF drug-screening results

## 1. A Knowledge Network of Molecular Mechanisms from the Neurofibromatosis Literature

In this section we put together an initial neurofibromatosis-specific knowledge network based on molecular interactions we have compiled from reading all available abstracts and full text articles from PubMed.

As background, we use multiple text mining systems from our collaborators and from the research community to extract raw causal relations and then assemble them using our knowledge assembly system, INDRA (the Integrated Network and Dynamical Reasoning Assembler). We do this systematically across all available literature and store the results in the INDRA Database for use in downstream projects like this one. The INDRA Database is publicly accessible at https://db.indra.bio. 

The first step in creating the EMMAA model for Neurofibromatosis is to find publications broadly relevant for neurofibromatosis. We do this by querying based on the both the term "neurofibromatosis" as well as the top-level Medical Subject Heading (MESH) term for Neurofibromatoses, D017253 (see https://www.ncbi.nlm.nih.gov/mesh/68017253). We use the `indra.literature` module to search PubMed using the PubMed REST API.

In [41]:
# Preliminaries
import os
import json
from collections import Counter
from mech_model.processor import NlModelProcessor
from indra.tools import assemble_corpus as ac
from indra.assemblers.pysb import PysbAssembler
from indra.explanation.model_checker.pysb import PysbModelChecker
from indra.literature import pubmed_client
from indra.pipeline import AssemblyPipeline
from indra.explanation.reporting import stmts_from_pysb_path
from indra.assemblers.english import EnglishAssembler

In [2]:
from emmaa.model import filter_eidos_ungrounded

INFO: [2020-11-13 21:49:36] covid_19.preprocess - Latest data release is 2020-11-13
INFO: [2020-11-13 21:49:37] pybel.config - no configuration found, using default sqlite connection sqlite:////Users/johnbachman/.pybel/pybel_0.14.0_cache.db
INFO: [2020-11-13 21:49:38] /Users/johnbachman/Dropbox/1johndata/Knowledge File/Biology/Research/Big Mechanism/adeft/adeft/recognize.py - OneShotRecognizer not available. AdeftLongformScorer has not been built successfully.
INFO: [2020-11-13 21:49:42] indra.preassembler.grounding_mapper.disambiguate - INDRA DB is not available for text content retrieval for grounding disambiguation.


In [3]:
# Query PubMed for articles related to NF
def get_nf_pmids():
    # PMIDs from text search for "neurofibromatosis"
    nf_text_pmids = pubmed_client.get_ids('neurofibromatosis')
    # Mesh term for neurofibromatoses
    nf_mesh_ids = pubmed_client.get_ids_for_mesh('D017253')
    return list(set(nf_text_pmids + nf_mesh_ids))

# Get the PMIDs
nf_pmids = get_nf_pmids()

Here's how many unique PMIDs we found:

In [4]:
len(nf_pmids)

17890

We then query the INDRA Database to get the INDRA Statements that have been extracted from these papers by text mining. One complication here is that for the EMMAA model we need to get raw, unassembled statements from the INDRA Database, which are currently not available from the public APIs (the public APIs provide access to the "finished", assembled statements). Therefore for this example we show the code that we run internally to obtain these statements but, by default, load the statements from a cache.

### How we initialize the model for assembly on EMMAA using direct INDRA DB Access

In [5]:
# Get raw statement IDs from the DB for the given TextRefs
reload = False
pmid_stmts_file = 'lit_model/nf_raw_stmts.pkl'
if reload: 
    db = get_primary_db()
    # Get statements for the given text refs
    print(f"Distilling statements for {len(nf_pmids)} TextRefs")
    start = time.time()
    clauses = [
        db.TextRef.pmid.in_(nf_pmids),
        db.TextContent.text_ref_id == db.TextRef.id,
        db.Reading.text_content_id == db.TextContent.id,
        db.RawStatements.reading_id == db.Reading.id]
    pmid_stmts = distill_stmts(db, get_full_stmts=True, clauses=clauses)
    end = time.time()
    elapsed = end - start
    print(elapsed)
    list(ac.dump_statements(pmid_stmts, pmid_stmts_file))
else:
    pmid_stmts = list(ac.load_statements(pmid_stmts_file))

INFO: [2020-11-13 21:49:45] indra.tools.assemble_corpus - Loading lit_model/nf_raw_stmts.pkl...
INFO: [2020-11-13 21:49:46] indra.tools.assemble_corpus - Loaded 20209 statements


Let's see how many statements we got:

In [6]:
len(pmid_stmts)

20209

### Preprocessing, filtering and deduplicating statements

The statements that we've obtained from the INDRA Database in the previous step represent raw output from NLP systems. We need to preprocess these statements in several ways: we need to fix named entity normalization, standardize sites of posttranslation modifications to canonical protein sequences, identify duplicate statements and overlapping statements, etc. The steps of this procedure are described in the `config.json` file for the EMMAA model. The EMMAA system reads the `config.json` file and runs assembly on the raw statements in AWS Batch. For illustration purposes we do this ourselves here.

In [8]:
# Load the config file
with open('lit_model/config.json', 'rt') as f:
    nf_config = json.load(f)

Here are the assembly steps for the model:
* `filter_no_hypothesis`. Filter out relations labeled by NLP systems as hypotheses (e.g. "we tested whether X causes Y")
* `ground_statements`. Runs entity normalization.
* `map_grounding`. Corrects common entity normalization errors and disambiguates entities using [Adeft](https://github.com/indralab/adeft).
* `filter_grounded_only`. Filters out any unnormalized entity texts. This can be removed to see if there are any useful entities that can't be linked to existing identifiers.
* `map_sequence`. Normalize sites of post-translational modification to canonical protein sequences. See ProtMapper [GitHub](https://github.com/indralab/protmapper) and [Preprint](https://www.biorxiv.org/content/10.1101/822668v3).
* `filter_eidos_ungrounded`. Filters out ungrounded entities in relations produced by the [Eidos](https://github.com/clulab/eidos) reader. 
* `run_preassembly`. Combine duplicate statements and organize statements by their relative specificity and detail.
* `filter_human_only`. Filter out references to non-human proteins.
* `filter_by_curation`. Filter out statements curated as incorrect. Note that because we don't have direct access to the INDRA Database to get these curations we skip this step that would run on EMMAA.

In [9]:
nf_config['assembly']

[{'function': 'filter_no_hypothesis'},
 {'function': 'ground_statements',
  'kwargs': {'mode': 'local', 'ungrounded_only': True}},
 {'function': 'ground_statements',
  'kwargs': {'mode': 'local',
   'sources': ['sparser'],
   'ungrounded_only': False}},
 {'function': 'map_grounding'},
 {'function': 'filter_grounded_only'},
 {'function': 'map_sequence'},
 {'function': 'filter_eidos_ungrounded'},
 {'function': 'run_preassembly', 'kwargs': {'return_toplevel': False}},
 {'function': 'filter_human_only'},
 {'function': 'filter_by_curation',
  'args': [{'function': 'get_curations'},
   'any',
   ['correct', 'act_vs_amt', 'hypothesis']],
  'kwargs': {'update_belief': True}}]

Remove the curation filter, as described above:

In [10]:
filter_by_curation_ix = 9
nf_config['assembly'].pop(filter_by_curation_ix)

{'function': 'filter_by_curation',
 'args': [{'function': 'get_curations'},
  'any',
  ['correct', 'act_vs_amt', 'hypothesis']],
 'kwargs': {'update_belief': True}}

Create the assembly pipeline and run:

In [11]:
ap = AssemblyPipeline(nf_config['assembly'])
pmid_stmts_asmb = ap.run(pmid_stmts)

INFO: [2020-11-13 21:50:02] indra.pipeline.pipeline - Running the pipeline
INFO: [2020-11-13 21:50:02] indra.pipeline.pipeline - Calling filter_no_hypothesis
INFO: [2020-11-13 21:50:02] indra.tools.assemble_corpus - Filtering 20209 statements to no hypothesis...
INFO: [2020-11-13 21:50:02] indra.tools.assemble_corpus - 19962 statements after filter...
INFO: [2020-11-13 21:50:02] indra.pipeline.pipeline - Calling ground_statements
INFO: [2020-11-13 21:50:12] gilda.grounder - Looking up the following strings: enzyme farnesyltransferase
INFO: [2020-11-13 21:50:12] gilda.grounder - Comparing enzyme farnesyltransferase with 0 entries
INFO: [2020-11-13 21:50:12] gilda.grounder - Looking up the following strings: dopamine
INFO: [2020-11-13 21:50:12] gilda.grounder - Comparing dopamine with 3 entries
INFO: [2020-11-13 21:50:12] gilda.grounder - Running disambiguation for dopamine
INFO: [2020-11-13 21:50:12] indra.ontology.bio.ontology - Loading INDRA bio ontology from cache at /Users/johnbachm

INFO: [2020-11-13 21:50:20] gilda.grounder - Comparing FPGL syndromes with 0 entries
INFO: [2020-11-13 21:50:20] gilda.grounder - Looking up the following strings: crl4 dcaf1
INFO: [2020-11-13 21:50:20] gilda.grounder - Comparing CRL4 DCAF1 with 0 entries
INFO: [2020-11-13 21:50:20] gilda.grounder - Looking up the following strings: polycomb repressive complex 2
INFO: [2020-11-13 21:50:20] gilda.grounder - Comparing polycomb repressive complex 2 with 3 entries
INFO: [2020-11-13 21:50:20] gilda.grounder - Running disambiguation for polycomb repressive complex 2
INFO: [2020-11-13 21:50:20] gilda.grounder - Looking up the following strings: homeobox
INFO: [2020-11-13 21:50:20] gilda.grounder - Comparing homeobox with 0 entries
INFO: [2020-11-13 21:50:20] gilda.grounder - Looking up the following strings: atra
INFO: [2020-11-13 21:50:20] gilda.grounder - Comparing ATRA with 1 entries
INFO: [2020-11-13 21:50:20] gilda.grounder - Running disambiguation for ATRA
INFO: [2020-11-13 21:50:20] gi

INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: calcium
INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing calcium with 4 entries
INFO: [2020-11-13 21:50:21] gilda.grounder - Running disambiguation for calcium
INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: patients who had had
INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing patients who had had with 0 entries
INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: expression of glycolytic enzymes and gfs and rtk akt signaling, expression of glycolytic enzymes and gfs and rtkakt signaling
INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing expression of glycolytic enzymes and GFs and RTK-AKT signaling with 0 entries
INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: pak, paks
INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing PAKs with 2 entries
INFO: [2020-11-13 21:50:21] gilda.grounder - Running disambigu

INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: small νmber of stopremoving variants in each category observed in gnomad, small number of stop removing variants in each category observed in gnomad, small number of stopremoving variants in each category observed in gnomad
INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing small number of stop-removing variants in each category observed in gnomAD with 0 entries
INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: power of maps
INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing power of MAPS with 0 entries
INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: sulindac
INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing Sulindac with 2 entries
INFO: [2020-11-13 21:50:21] gilda.grounder - Running disambiguation for Sulindac
INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: pdgf beta, pdgfbeta, pdgfb, pdgfβ
INFO: [2020-11

INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing high-impact uAUGs with 0 entries
INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: silica
INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing silica with 2 entries
INFO: [2020-11-13 21:50:21] gilda.grounder - Running disambiguation for silica
INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: dosage of bet inhibitor necessary for in vivo mpnst treatment
INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing dosage of BET inhibitor necessary for in vivo MPNST treatment with 0 entries
INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: gtp
INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing GTP with 4 entries
INFO: [2020-11-13 21:50:21] gilda.grounder - Running disambiguation for GTP
INFO: [2020-11-13 21:50:21] gilda.grounder - Looking up the following strings: ras erk, raserk
INFO: [2020-11-13 21:50:21] gilda.grounder - Comparing RAS-ERK with 0

...

INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for EPHA4
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: ephb2
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing EPHB2 with 1 entries
INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for EPHB2
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: nrg1
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing NRG1 with 2 entries
INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for NRG1
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: erbb2
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing erbB2 with 2 entries
INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for erbB2
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: erbb3
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing erbB3 with 2 entries
INFO: [2020-11-13 21:51:16] gilda.grounder - Ru

INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for SHP2
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: merlin
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing merlin with 3 entries
INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for merlin
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: kinases, mkk4 and mkk6
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing kinases, MKK4 and MKK6 with 0 entries
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: p38 sapk
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing p38 SAPK with 1 entries
INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for p38 SAPK
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: integrin
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing integrin with 1 entries
INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for

INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for TP73
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: nf1
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing NF1 with 1 entries
INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for NF1
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: ereg
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing EREG with 1 entries
INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for EREG
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: nf1
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing NF1 with 1 entries
INFO: [2020-11-13 21:51:16] gilda.grounder - Running disambiguation for NF1
INFO: [2020-11-13 21:51:16] gilda.grounder - Looking up the following strings: mutations, μtations, mutation
INFO: [2020-11-13 21:51:16] gilda.grounder - Comparing mutations with 2 entries
INFO: [2020-11-13 21:51:16] gild

INFO: [2020-11-13 21:51:17] gilda.grounder - Comparing NF1 with 1 entries
INFO: [2020-11-13 21:51:17] gilda.grounder - Running disambiguation for NF1
INFO: [2020-11-13 21:51:17] gilda.grounder - Looking up the following strings: fmrp
INFO: [2020-11-13 21:51:17] gilda.grounder - Comparing FMRP with 1 entries
INFO: [2020-11-13 21:51:17] gilda.grounder - Running disambiguation for FMRP
INFO: [2020-11-13 21:51:17] gilda.grounder - Looking up the following strings: potassium channel
INFO: [2020-11-13 21:51:17] gilda.grounder - Comparing potassium channel with 3 entries
INFO: [2020-11-13 21:51:17] gilda.grounder - Running disambiguation for potassium channel
INFO: [2020-11-13 21:51:17] gilda.grounder - Looking up the following strings: amot
INFO: [2020-11-13 21:51:17] gilda.grounder - Comparing Amot with 1 entries
INFO: [2020-11-13 21:51:17] gilda.grounder - Running disambiguation for Amot
INFO: [2020-11-13 21:51:17] gilda.grounder - Looking up the following strings: merlin
INFO: [2020-11-13

INFO: [2020-11-13 21:53:35] indra.preassembler.grounding_mapper.mapper - 466 statements filtered out
INFO: [2020-11-13 21:53:35] indra.pipeline.pipeline - Calling filter_grounded_only
INFO: [2020-11-13 21:53:35] indra.tools.assemble_corpus - Filtering 19496 statements for grounded agents...
INFO: [2020-11-13 21:53:35] indra.tools.assemble_corpus - 15130 statements after filter...
INFO: [2020-11-13 21:53:35] indra.pipeline.pipeline - Calling map_sequence
INFO: [2020-11-13 21:53:35] indra.tools.assemble_corpus - Mapping sites on 15130 statements...
INFO: [2020-11-13 21:53:46] protmapper.uniprot_client - Loading Swissprot sequences...
INFO: [2020-11-13 21:53:49] protmapper.uniprot_client - Loading Uniprot isoform sequences...
INFO: [2020-11-13 21:53:55] indra.tools.assemble_corpus - 15077 statements with valid sites
INFO: [2020-11-13 21:53:55] indra.pipeline.pipeline - Calling filter_eidos_ungrounded
INFO: [2020-11-13 21:53:55] emmaa.model - Filtering out ungrounded Eidos statements from 

After assembly, the total number of statements should be substantially lower, since we have combined redundant statements and filtered out ones with ungrounded entities:

In [13]:
len(pmid_stmts_asmb)

7693

## 2. A Mechanistic Ras-NF Model from Natural Language

Next we show how a second, distinct Ras-NF mechanistic model can be automatically assembled from a set of manually curated sentences describing molecular interactions. We call this approach "natural language modeling" and it is described in detail in our paper:

Gyori B.M.\*, Bachman J.A.\*, Subramanian K., Muhlich J.L., Galescu L., Sorger P.K. From word models to executable models of signaling networks using automated assembly (2017), Molecular Systems Biology, 13, 954. (https://www.embopress.org/doi/full/10.15252/msb.20177651)


### Getting the statements from text

In this step we process the assertions in the text file `ras_nf_model.rst` into INDRA Statements. Each sentence is processed individually and the statements for each sentence are stored in a local cache. Processing can take several minutes.

In [17]:
model_text_file = 'mech_model/ras_nf_model.rst'
stmt_output_file = 'mech_model/ras_nf_stmts.pkl'

# Create cache directory
if not os.path.exists('mech_model/cache'):
    os.makedirs('mech_model/cache')
nlmp = NlModelProcessor(model_text_file, cache_dir='mech_model/cache', trips_endpoint='drum-dev')
ras_stmts = nlmp.get_statements(stmt_output_file)

Processing group 'EGFR Pathway'...
1 of 13: processing 'EGF binds to EGFR.'...
Loading cached stmts: EGFbindstoEGFR.pkl
2 of 13: processing 'EGFR bound to EGF binds EGFR bound to EGF.'...
Loading cached stmts: EGFRboundtoEGFbindsEGFRboundtoEGF.pkl
3 of 13: processing 'EGFR bound to EGFR phosphorylates itself at Y1016.'...
Loading cached stmts: EGFRboundtoEGFRphosphorylatesitselfatY1016.pkl
4 of 13: processing 'EGFR bound to EGFR phosphorylates itself at Y1069.'...
Loading cached stmts: EGFRboundtoEGFRphosphorylatesitselfatY1069.pkl
5 of 13: processing 'EGFR bound to EGFR phosphorylates itself at Y1092.'...
Loading cached stmts: EGFRboundtoEGFRphosphorylatesitselfatY1092.pkl
6 of 13: processing 'EGFR bound to EGFR phosphorylates itself at Y1110.'...
Loading cached stmts: EGFRboundtoEGFRphosphorylatesitselfatY1110.pkl
7 of 13: processing 'EGFR bound to EGFR phosphorylates itself at Y1138.'...
Loading cached stmts: EGFRboundtoEGFRphosphorylatesitselfatY1138.pkl
8 of 13: processing 'EGFR b

ERROR: [2020-11-13 21:55:46] indra.sources.trips.client - Problem with TRIPS query: status code 500
ERROR: [2020-11-13 21:55:47] indra.sources.trips.client - Problem with TRIPS query: status code 500


No statements for "Rac1 and downstream signaling into the MAPK pathway.""
9 of 58: processing 'NF2 binds AMOT.'...
Loading cached stmts: NF2bindsAMOT.pkl
10 of 58: processing 'ARHGAP17 binds AMOT not bound to NF2.'...
Loading cached stmts: ARHGAP17bindsAMOTnotboundtoNF2.pkl
11 of 58: processing 'ARHGAP17 not bound to AMOT inhibits RAC1.'...
Loading cached stmts: ARHGAP17notboundtoAMOTinhibitsRAC1.pkl
12 of 58: processing 'ARHGAP17 not bound to AMOT inhibits CDC42.'...
Loading cached stmts: ARHGAP17notboundtoAMOTinhibitsCDC42.pkl
13 of 58: processing 'PAK1 binds active CDC42.'...
Loading cached stmts: PAK1bindsactiveCDC42.pkl
14 of 58: processing 'PAK1 bound to CDC42 phosphorylates itself.'...
Loading cached stmts: PAK1boundtoCDC42phosphorylatesitself.pkl
15 of 58: processing 'PAK1 binds active RAC1.'...
Loading cached stmts: PAK1bindsactiveRAC1.pkl
16 of 58: processing 'PAK1 bound to RAC1 phosphorylates itself.'...
Loading cached stmts: PAK1boundtoRAC1phosphorylatesitself.pkl
17 of 58:

ERROR: [2020-11-13 21:55:47] indra.sources.trips.client - Problem with TRIPS query: status code 500


No statements for "APP binds NF1."
50 of 58: processing 'GRB10 inhibits RAS.'...
Loading cached stmts: GRB10inhibitsRAS.pkl
51 of 58: processing 'NF2 binds CTNNA.'...
Loading cached stmts: NF2bindsCTNNA.pkl
52 of 58: processing 'LAYN binds NF2.'...
Loading cached stmts: LAYNbindsNF2.pkl
53 of 58: processing 'NF1 binds DDAH1.'...
Loading cached stmts: NF1bindsDDAH1.pkl
54 of 58: processing 'PKA phosphorylates NF1 bound to DDAH1.'...
Loading cached stmts: PKAphosphorylatesNF1boundtoDDAH1.pkl
55 of 58: processing 'JNK phosphorylates PXN at S178.'...
Loading cached stmts: JNKphosphorylatesPXNatS178.pkl
56 of 58: processing 'MDM2 binds TP53.'...
Loading cached stmts: MDM2bindsTP53.pkl
57 of 58: processing 'MDM2 ubiquitinates TP53.'...
Loading cached stmts: MDM2ubiquitinatesTP53.pkl
58 of 58: processing 'Ubiquitinated TP53 is degraded.'...
Loading cached stmts: UbiquitinatedTP53isdegraded.pkl
Processing group 'PI-3-kinase and AKT pathway'...
1 of 23: processing 'PIK3CA binds KRAS that is at 

ERROR: [2020-11-13 21:55:47] indra.sources.trips.client - Problem with TRIPS query: status code 500
ERROR: [2020-11-13 21:55:47] indra.sources.trips.client - Problem with TRIPS query: status code 500


No statements for "EIF4E increases translational initiation."
9 of 9: processing 'EIF4E increases cell proliferation.'...
Loading cached stmts: EIF4Eincreasescellproliferation.pkl
Processing group 'mTORC2'...
1 of 2: processing 'MTOR not bound to RPTOR binds to RICTOR.'...
Loading cached stmts: MTORnotboundtoRPTORbindstoRICTOR.pkl
2 of 2: processing 'Active MTOR bound to RICTOR phosphorylates AKT1 at S473.'...
Loading cached stmts: ActiveMTORboundtoRICTORphosphorylatesAKT1atS473.pkl
Processing group 'AKT1S1'...
1 of 3: processing 'Active AKT1 phosphorylates AKT1S1 at T246.'...
Loading cached stmts: ActiveAKT1phosphorylatesAKT1S1atT246.pkl
2 of 3: processing 'AKT1S1 phosphorylated at T246 binds 14-3-3 proteins.'...
Loading cached stmts: AKT1S1phosphorylatedatT246binds14-3-3proteins.pkl
3 of 3: processing 'AKT1S1 not bound to 14-3-3 proteins binds to MTOR.'...
Loading cached stmts: AKT1S1notboundto14-3-3proteinsbindstoMTOR.pkl
Processing group 'MAPK substrates and effectors'...
1 of 8: p

INFO: [2020-11-13 21:55:47] indra.tools.assemble_corpus - Dumping 210 statements into mech_model/ras_nf_stmts.pkl...


Loading cached stmts: ActiveRPS6KB1phosphorylatesRPS6atS235andS240.pkl
3 of 3: processing 'RPS6 phosphorylated at S235 and S240 is active.'...
Loading cached stmts: RPS6phosphorylatedatS235andS240isactive.pkl
Processing group 'Protein Kinase C'...
1 of 4: processing 'Active PRKCA phosphorylates GSK3A at serine 21.'...
Loading cached stmts: ActivePRKCAphosphorylatesGSK3Aatserine21.pkl
2 of 4: processing 'Active PRKCA phosphorylates PEBP1 at S153.'...
Loading cached stmts: ActivePRKCAphosphorylatesPEBP1atS153.pkl
3 of 4: processing 'Active PRKCA phosphorylates NF1 on serine.'...
Loading cached stmts: ActivePRKCAphosphorylatesNF1onserine.pkl
4 of 4: processing 'Active RPS6KA1 phosphorylates RPS6 at S235.'...
Loading cached stmts: ActiveRPS6KA1phosphorylatesRPS6atS235.pkl
Processing group 'Rac family GTPases'...
1 of 3: processing 'Active SRC phosphorylates TIAM1.'...
Loading cached stmts: ActiveSRCphosphorylatesTIAM1.pkl
2 of 3: processing 'Phosphorylated TIAM1 is active.'...
Loading cach

Let's see how many statements we have:

In [18]:
len(ras_stmts)

210

The NLP system we're using for this, called TRIPS (developed by the Institute for Human and Machine Cognition, IHMC), sometimes grounds the text "NF1" as a cell line instead of as the gene/protein. So we fix that here using the INDRA `map_grounding` function.

In [19]:
# Grounding map the statements
grounding_map = {'NF1': {'HGNC': '7765'}}
ras_stmts = ac.map_grounding(ras_stmts, do_rename=True, grounding_map=grounding_map)

INFO: [2020-11-13 21:56:00] indra.tools.assemble_corpus - Mapping grounding on 210 statements...
INFO: [2020-11-13 21:56:00] indra.preassembler.grounding_mapper.disambiguate - INDRA DB is not available for text content retrieval for grounding disambiguation.
INFO: [2020-11-13 21:56:00] indra.preassembler.grounding_mapper.disambiguate - Falling back on sentence-based disambiguation
INFO: [2020-11-13 21:56:00] indra.preassembler.grounding_mapper.mapper - 0 statements filtered out


Here's what the statements we got out of the sentences look like:

In [21]:
ras_stmts

[Complex(EGF(), EGFR()),
 Complex(EGFR(bound: [EGF, True]), EGFR(bound: [EGF, True])),
 Autophosphorylation(EGFR(bound: [EGFR, True]), Y, 1016),
 Autophosphorylation(EGFR(bound: [EGFR, True]), Y, 1069),
 Autophosphorylation(EGFR(bound: [EGFR, True]), Y, 1092),
 Autophosphorylation(EGFR(bound: [EGFR, True]), Y, 1110),
 Autophosphorylation(EGFR(bound: [EGFR, True]), Y, 1138),
 Autophosphorylation(EGFR(bound: [EGFR, True]), Y, 1172),
 Autophosphorylation(EGFR(bound: [EGFR, True]), Y, 1197),
 Phosphorylation(EGFR(bound: [EGFR, True]), SRC(), Y, 419),
 Phosphorylation(EGFR(bound: [EGFR, True]), SRC()),
 ActiveForm(SRC(mods: (phosphorylation, Y, 419)), activity, True),
 Phosphorylation(SRC(activity), EGFR(), Y, 869),
 Complex(IGF1R(), IGF1R()),
 Autophosphorylation(IGF1R(bound: [IGF1R, True]), Y, 1166),
 ActiveForm(IGF1R(mods: (phosphorylation, Y, 1166)), activity, True),
 Phosphorylation(IGF1R(activity), IRS1(), Y),
 ActiveForm(IRS1(mods: (phosphorylation, Y)), activity, True),
 Complex(IRS

### Assembling an executable PySB model from the curated sentences

To explain the claims that we extracted from the text mined NF model, we take our detailed natural language model and assemble it into a rule-based executable model using INDRA and PySB. For more on PySB see our previous paper:

Lopez C.F.\*, Muhlich J.L.\*, Bachman J.A.\*, Sorger P.K. Programming biological models in Python using PySB (2013), Molecular Systems Biology, 9, 646. (https://www.embopress.org/doi/full/10.1038/msb.2013.1)

In [22]:
pa = PysbAssembler(ras_stmts)
pysb_model = pa.make_model()

INFO: [2020-11-13 21:57:28] indra.assemblers.pysb.assembler - Using default assembly policy.


Getting parents for ('HGNC', '20249')
Getting parents for ('HGNC', '7765')
Getting parents for ('HGNC', '11714')
Getting parents for ('HGNC', '16262')
Getting parents for ('HGNC', '8975')
Getting parents for ('HGNC', '6407')
Getting parents for ('HGNC', '8975')
Getting parents for ('HGNC', '6125')
Getting parents for ('HGNC', '8816')
Getting parents for ('HGNC', '8993')
Getting parents for ('HGNC', '12363')
Getting parents for ('HGNC', '12362')
Getting parents for ('HGNC', '12362')
Getting parents for ('HGNC', '12363')
Getting parents for ('HGNC', '3942')
Getting parents for ('HGNC', '28426')
Getting parents for ('HGNC', '3942')
Getting parents for ('HGNC', '10011')
Getting parents for ('HGNC', '6769')
Getting parents for ('HGNC', '6770')
Getting parents for ('HGNC', '9829')
Getting parents for ('HGNC', '8630')
Getting parents for ('HGNC', '3942')
Getting parents for ('HGNC', '30287')
Getting parents for ('HGNC', '3942')
Getting parents for ('HGNC', '30287')
Getting parents for ('HGNC'

The model consists of 250 causal rules describing the interactions among 94 distinct agents:

In [24]:
pysb_model

<Model 'indra_model' (monomers: 94, rules: 250, parameters: 344, expressions: 0, compartments: 0) at 0x7f8e02ac9990>

## 3. Checking the NF literature findings against our detailed model

Next we use the model checker component within INDRA to see how many of findings from our text mined NF model can be explained with the detailed mechanisms we've explicitly curated in our natural language model.

In [48]:
pmc = PysbModelChecker(pysb_model, pmid_stmts_asmb)
mc_results = pmc.check_model(max_path_length=20)

INFO: [2020-11-13 22:31:07] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:07] indra.explanation.model_checker.model_checker - Checking statement (1/7693): Acetylation(diboron(), ALB())
INFO: [2020-11-13 22:31:07] indra.assemblers.pysb.assembler - No monomer found corresponding to agent ALB(mods: (acetylation))
INFO: [2020-11-13 22:31:07] indra.assemblers.pysb.assembler - No monomer found corresponding to agent Histone(mods: (acetylation))
INFO: [2020-11-13 22:31:07] indra.assemblers.pysb.assembler - No monomer found corresponding to agent SMC3(mods: (acetylation))
INFO: [2020-11-13 22:31:07] indra.assemblers.pysb.assembler - No monomer found corresponding to agent Histone(mods: (acetylation))
INFO: [2020-11-13 22:31:07] indra.assemblers.pysb.assembler - No monomer found corresponding to agent protein(mods: (acetylation))
INFO: [2020-11-13 22:31:07] indra.assemblers.pysb.assembler - No monomer found corresponding to agent Cyclin_A(mods: (acetylation))
INFO:

INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent cell differentiation(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent CRABP2(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent apoptotic process(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent cell death(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent adenosine 5'-monophosphate(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent calcium(2+)(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent metabolic process(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent 

INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent phosphate(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent vitamin D(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent G_alpha(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent PTH(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent homeostatic process(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent HIF1A(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent NR3C2(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent Magnetic Resonance Imaging(activity)
INFO: [2020-1

INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent G_alpha(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent ADCY1(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent DHPS(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent sirolimus(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent ETV5(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent 3',5'-cyclic GMP(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent (R)-noradrenaline(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent Normetanephrine(activity)
INFO: [2020-11-13 2

INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent TNFSF10(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent MAPK(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent cell differentiation(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent N-methyl-D-aspartic acid(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent apoptotic process(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent AKT(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent CALM(activity)
INFO: [2020-11-13 22:31:08] indra.assemblers.pysb.assembler - No monomer found corresponding to agent ERK(activity)
INFO: [2020-11

...

INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7582/7693): Translocation(SOS(), None, plasma membrane)
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - Statement type Translocation not handled
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7583/7693): Translocation(mTORC1(), None, lysosomal membrane)
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - Statement type Translocation not handled
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7584/7693): Translocation(SRC(), None, focal adhesion)
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - Statement type Translocation not handled
INFO: [2020-11-13 22:31:54] indra.explanation.model_che

INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - Statement type Translocation not handled
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7607/7693): Translocation(IQCJ-SCHIP1(), None, growth cone)
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - Statement type Translocation not handled
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7608/7693): Translocation(AKT1(), None, plasma membrane)
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - Statement type Translocation not handled
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7609/7693): Translocation(GFER(

INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7631/7693): Translocation(NF2(), None, nucleus)
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - Statement type Translocation not handled
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7632/7693): Translocation(NF2(), None, plasma membrane)
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - Statement type Translocation not handled
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7633/7693): Translocation(NF2(), cytoplasm, None)
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - Statement type Translocation not handled
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker 

INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - No observables for stmt Ubiquitination(FBXW7(), NFIC()), returning False
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7655/7693): Ubiquitination(CDC20(), APC())
INFO: [2020-11-13 22:31:54] indra.assemblers.pysb.assembler - No monomer found corresponding to agent CDC20()
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7656/7693): Ubiquitination(IL17RB(), LAT())
INFO: [2020-11-13 22:31:54] indra.assemblers.pysb.assembler - No monomer found corresponding to agent IL17RB()
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7657/7693): Ubiquitinati

INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - No observables for stmt Ubiquitination(None, CDH2()), returning False
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7678/7693): Ubiquitination(None, IL17RB())
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - No observables for stmt Ubiquitination(None, IL17RB()), returning False
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - Checking statement (7679/7693): Ubiquitination(None, LAT())
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.pysb - No observables for stmt Ubiquitination(None, LAT()), returning False
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker - ---
INFO: [2020-11-13 22:31:54] indra.explanation.model_checker.model_checker

The results consist of a list of tuples showing the statement that was checked and a PathResult object indicating whether a path was found, and if so, what the path was.

In [49]:
mc_results[0]

(Acetylation(diboron(), ALB()), 
 PathResult:
     path_found: False
     result_code: SUBJECT_MONOMERS_NOT_FOUND
     path_metrics: []
     paths: []
     max_paths: 1
     max_path_length: 20)

First let's see how many of the tests were satisfied and if not, why not.

In [50]:
rc_ctr = Counter([res[1].result_code for res in mc_results])
rc_ctr

Counter({'SUBJECT_MONOMERS_NOT_FOUND': 4466,
         'OBSERVABLES_NOT_FOUND': 1551,
         'NO_PATHS_FOUND': 153,
         'INPUT_RULES_NOT_FOUND': 31,
         'PATHS_FOUND': 179,
         'STATEMENT_TYPE_NOT_HANDLED': 1313})

Not surprisingly, the majority of the tests failed with result code `SUBJECT_MONOMERS_NOT_FOUND` or `OBSERVABLES_NOT_FOUND`, meaning the test statement referred to entities not actually in the explanatory model. This is not surprising since the curated model is much smaller. The test statements that don't overlap can be analyzed to determine which entities should be added next. However, let's first look at some statements that passed:

In [51]:
passed_res = [res for res in mc_results if res[1].path_found]

Let's look at an explanation for how BRAF activates cell proliferation. Here is the full PathResult object:

In [56]:
passed_res[6]

(Activation(BRAF(), cell population proliferation()), 
 PathResult:
     path_found: True
     result_code: PATHS_FOUND
     path_metrics: 
         0: source_node: ('BRAF_phospho_phosphorylation_MAP2K1_S218', 0), target_node: ('cell_population_proliferation_activity_active_obs', 0), length: 9
         1: source_node: ('BRAF_phospho_phosphorylation_MAP2K1_S222', 0), target_node: ('cell_population_proliferation_activity_active_obs', 0), length: 9
         2: source_node: ('BRAF_phospho_phosphorylation_MAP2K1_S218', 0), target_node: ('cell_population_proliferation_activity_active_obs', 0), length: 9
         3: source_node: ('BRAF_phospho_phosphorylation_MAP2K1_S222', 0), target_node: ('cell_population_proliferation_activity_active_obs', 0), length: 9
         4: source_node: ('KRAS_act_BRAF_bind', 0), target_node: ('cell_population_proliferation_activity_active_obs', 0), length: 11
         5: source_node: ('KRAS_BRAF_dissociate', 0), target_node: ('cell_population_proliferation_activit

And just the path found:

In [58]:
path = passed_res[6][1].paths[0]
path

(('BRAF_phospho_phosphorylation_MAP2K1_S218', 0),
 ('MAP2K1_phosphoS218_phosphoS222_phosphorylation_MAPK1_T185', 0),
 ('MAPK1_phosphoT185_phosphoY187_phosphorylation_ELK1_S383', 0),
 ('ELK1_phosphoS383_phosphoS389_produces_FOS', 0),
 ('FOS_JUN_bind', 0),
 ('FOS_JUN_produces_CCND1', 0),
 ('CCND1_CDK4_bind', 0),
 ('CDK4_CCND1_phosphorylation_RB1_S807', 0),
 ('RB1_phosphoS807_deactivates_cell_population_proliferation_activity', 1),
 ('cell_population_proliferation_activity_active_obs', 0))

The path is over the model rules. The list of rules can be mapped back into the INDRA Statements from the curated model used for explanation:

In [61]:
braf_path_stmts = stmts_from_pysb_path(path, pysb_model, ras_stmts)
braf_path_stmts

[Phosphorylation(BRAF(activity), MAP2K1(), S, 218),
 Phosphorylation(MAP2K1(activity), MAPK1(), T, 185),
 Phosphorylation(MAPK1(activity), ELK1(), S, 383),
 IncreaseAmount(ELK1(activity, location: nucleus), FOS()),
 Complex(FOS(), JUN()),
 IncreaseAmount(FOS(bound: [JUN, True]), CCND1()),
 Complex(CCND1(), CDK4()),
 Phosphorylation(CDK4(bound: [CCND1, True]), RB1(), S, 807),
 Inhibition(RB1(activity), cell population proliferation())]

To make this even more human-interpretable, we can render our explanation for the effect of BRAF on proliferation in English:

In [64]:
ea = EnglishAssembler(braf_path_stmts)
print(ea.make_model())

Active BRAF phosphorylates MAP2K1 on S218. Active MAP2K1 phosphorylates MAPK1 on T185. Active MAPK1 phosphorylates ELK1 on S383. Active ELK1 in the nucleus increases the amount of FOS. FOS binds JUN. FOS bound to JUN increases the amount of CCND1. CCND1 binds CDK4. CDK4 bound to CCND1 phosphorylates RB1 on S807. Active RB1 inhibits cell population proliferation.
